In [ ]:
import matplotlib
%matplotlib inline
import numpy
import os
import datetime
import scipy.interpolate
# Import constants
import constant
#Import advection tools
import tools_advection
# Create once the collection for this notebook
collection_id = None
import SEAScope.lib.utils
SEAScope.lib.utils.init_ids(50, 5000)
_ind = 0

## Load and select data
<span style="color:green">**Select the velocity you want to validate, select a timespan of one week **<br>
**Draw a polygon on SEASCope**<br>
**Click on the extract button on the polygon window**<br>
</span>


In [ ]:
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()
granule_id = None

**Load an old data data directly from a serialized extraction using the path printed on terminal <br>
(eg data_path = '/tmp/tmpcdemmhcb20170621TJun061498041719/seascope_extract.pyo')** <br>
Not used in this training, if you want to load old data: uncomment the following cell and fill data_path value

#from SEAScope.lib import load_pyo
#data_path = ''
#extractions = load_pyo(data_path)
## Print a list of path of extracted granules 
print('\n'.join(extractions.keys()))

**Print selected granules**

In [ ]:
for k, data in enumerate(extractions.keys()):
    print('{} - {}'.format(k, os.path.basename(data)))
    print('\n'.join(['\t{}'.format(x) for x in extractions[data]['data']]))
    print(extractions[data]['meta']['start'])

<span style="color:red">**Choose numbers corresponding to geostrophic current in chronological order**</span>

In [ ]:
k_u = [3, 2, 7, 4, 0, 6, 5, 1] # /!\ You may need to adapt this variable 
                               # and comment the following lines if you 
                              # have selected several collections
# If you have only selected current you can compute k_u automatically
#Uncomment the following lines
list_name = []
list_date = []
for k, data in enumerate(extractions.keys()):
    list_name.append(os.path.basename(data))
    list_date.append(extractions[data]['meta']['start'])
k_u = sorted(range(len(list_date)), key=list_date.__getitem__)
print(k_u)


## Play with the data
** Compute trajectory of fictive particules at initial position (x0, y0) using velocity: <br>
$ x = x_0 + u * dt$<br>
$ y = y_0 + v * dt$**

<span style="color:red">** Fill variable name for your selected velocity **</span>

In [ ]:
# Get longitudes, latitudes from gcps and time from first granule
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == k_u[0])
extraction = extractions[granule_uri]
start = extraction['meta']['start']
print(extraction['meta']['fields'])

In [ ]:
# Initialize particule position with the initial position of your drifter
# /!\ You may need to adapt these variables 
part_lat = -41.8
part_lon = 20.22

# Total time of advection (smaller than the number of days for the loaded velocity) in days
# /!\ You may need to adapt this variable 
tadv = 5
# Time step for advection (in day)
# /!\ You may need to adapt this variable 
time_step = 0.2

granule_id = None

In [ ]:
### Set name_var_u, name_var_v
name_var_u = 'eastward_eulerian_current_velocity'  # /!\ You may need to adapt this variable
name_var_v = 'northward_eulerian_current_velocity' # /!\ You may need to adapt this variable
#name_var_u = 'u_geo' # /!\ You may need to adapt this variable 
#name_var_v = 'v_geo' # /!\ You may need to adapt this variable 
# Get and concatenate velocity variable
u_vel = []
v_vel = []
for ind in k_u:
    granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == ind )
    extraction = extractions[granule_uri]  
    u_vel.append(extraction['data'][name_var_u])
    v_vel.append(extraction['data'][name_var_v])

from SEAScope.lib.utils import get_lonlat
lon2D, lat2D = get_lonlat(extraction, numpy.shape(u_vel[0]))

# Advect particles
traj_lon, traj_lat, adv_time = tools_advection.advection(part_lon,
                                part_lat, lon2D, lat2D, u_vel,
                                v_vel, tadv, time_step)
stop_dt = start + datetime.timedelta(days=adv_time[-1])

# Trajectory time
traj_time = []
start_ref = datetime.datetime(2015,12,1)
for i in range(len(adv_time)):
    traj_dt = (start + datetime.timedelta(days=adv_time[i]) - start_ref)
    traj_time.append(traj_dt.days)

**Plot variables <br>
You can try to plot ugeo (zonal componant), vgeo (meridional componant), the velocity norm, the ssh ... **

In [ ]:
matplotlib.pyplot.scatter(traj_lon, traj_lat, c=traj_time, cmap='jet')
matplotlib.pyplot.colorbar()  

## Export velocity to SEAScope

In [ ]:
import json
import datetime
import numpy
import seascope_export
from SEAScope.lib.utils import create_collection, create_variable
from SEAScope.lib.utils import create_granule, set_field

**Define Collection:** <br>
** A granule has to belong to a collection **<br>
<span style="color:red"> **Enter a name for the collection (collection_name)**</span>

In [ ]:
if collection_id is None:
    # Collection
    collection_name = 'User - Virtual drifter 2'
    # Create collection
    collection_id, collection = create_collection(collection_name)
    # Collection
    # IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155
import SEAScope.upload
with SEAScope.upload.connect(host, port) as link:
# Send create collection job
    SEAScope.upload.collection(link, collection)

**Upload granule to SEAScope: <br>
Define shell of granule, create granule <br>
The granule will contain each matrix of modified data as what we call a "field"<br>**
<span style="color:red">** Enter a name for each field (field_name_time) **</span></br>
**Upload collection and granule to SEAScope**

In [ ]:
# Shell of Granule
# Each position of the trajectory will be used as GCP
gcps = []
for i in range(0, len(traj_lon)):
    gcp = {'lon': traj_lon[i], 'lat': traj_lat[i], 'i': i, 'j': 0}
    gcps.append(gcp)

# Create granule
if granule_id is None:
    granule_id, granule = create_granule(collection_id, gcps, start, stop_dt)

# Set variables
# Enter a name for each variable field
from SEAScope.lib.utils import set_field
field_name_time ='time'
set_field(granule, field_name_time, traj_time)

#Upload collection and granule to SEAScope
with SEAScope.upload.connect(host, port) as link:   
    SEAScope.upload.granule(link, granule)
seascope_export.upload_granule(collection, granule)

**Telling SEAScope what to display: <br>
 The next step is variables definition. ** <br>
**<span style="color:red"> Enter a name for each variable you want to display (variable_name_time, ...) </span>**</br>

In [ ]:
# Create a variable for each parameter
variable_name_time = 'time_{}'.format(_ind)
var1 = create_variable(collection, variable_name_time, [field_name_time], dims=1)


# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)
_ind += 1

** Telling SEAScope how to display variables: <br>
The rendering options are defined in the following cell. <br>
<span style="color:red"> You can play with min, max values, the colormap ... and check how the rendering changes on SEAScope </span>
**

In [ ]:
# Rendering configuration for the time
rcfg1 = var1['rendering']
rcfg1['min'] = 1
rcfg1['max'] = 31
rcfg1['colormap'] = 'monthly'
rcfg1['zindex'] = .923

# Upload to SEAScope
seascope_export.upload_config(rcfg1)

<span style="color:green">** Go back to SEAScope and visually compare your virtual drifter trajectory with AOML drifters <br> 
play with range, colorbar, transparancy ...**</span>